In [1]:
from google.colab import drive
drive.mount('/content/drive/')

Mounted at /content/drive/


In [2]:
!pip install sentencepiece

     |████████████████████████████████| 1.2MB 4.3MB/s 


In [3]:
%%capture
!pip install transformers

In [4]:
import torch
import numpy as np
import pandas as pd
import torch.nn as nn

import transformers
from sklearn.metrics import *
from transformers import AdamW
from tqdm.notebook import tqdm
from scipy.special import softmax
from sklearn.metrics import classification_report
from sklearn.model_selection import train_test_split as tts
from transformers import BertTokenizerFast, BertConfig, BertForSequenceClassification, AutoModel
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler

In [5]:
# Define the device
device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')

#### Download

In [6]:
cd drive/My Drive/Colab Notebooks/experiments

/content/drive/My Drive/Colab Notebooks/experiments


In [7]:
# Download humor detection data
# Paper: https://arxiv.org/abs/2004.12765
data = pd.read_csv("data/trofi.csv")
print("\nThere are", len(data), "sentences")

# Use the standard text/label columns
# Create labels: 1 --> humorous, 0 --> not humorous
#data = data.dropna()
data["label"] = data["label"].apply(int)
data.head()


There are 3737 sentences


verb                                           sentence  verb_idx  label
0  absorb  An Energy Department spokesman says the sulfur...        22      0
1  absorb  The yellow beta carotene pigment absorbs blue ...         5      0
2  absorb  This time , the ground absorbed the shock wave...         5      0
3  absorb  '' Vitamins could be passed right out of the b...        12      0
4  absorb  As Eliot wrote : '' In a warm haze , the sultr...        14      0

#### Split to training, validation and test



In [8]:
# Use a subset for quick experiments
#data = data[:10000]

# Split to train, val and test
train, test = tts(data[["sentence", "label"]], random_state=42, test_size=0.1)
train, val = tts(train, random_state=42, test_size=test.shape[0])

#### Tokenize and encode with BERT tokenizer

In [9]:
from transformers import XLMRobertaForSequenceClassification

output_dir = 'stockholm/xlm_code/trofi_xlmroberta/xlm-roberta_model_save'

print(output_dir)

stockholm/xlm_code/trofi_xlmroberta/xlm-roberta_model_save


In [10]:
from transformers import XLMRobertaTokenizer
import torch
# Load the BERT tokenizer.
print('Loading XLMRobertaTokenizer...')
bert_tokenizer = XLMRobertaTokenizer.from_pretrained(output_dir)
model_e = XLMRobertaForSequenceClassification.from_pretrained(output_dir, num_labels = 2, output_attentions = True, output_hidden_states = True,)

Loading XLMRobertaTokenizer...


Some weights of the model checkpoint at stockholm/xlm_code/trofi_xlmroberta/xlm-roberta_model_save were not used when initializing XLMRobertaForSequenceClassification: ['roberta.pooler.dense.bias', 'roberta.pooler.dense.weight']
- This IS expected if you are initializing XLMRobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing XLMRobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [11]:
MAX_LEN = 21 # This value could be set as 256, 512 etc.

encoded_instance = bert_tokenizer.encode_plus(
            train.iloc[0].sentence,
            truncation = True,                
            add_special_tokens = True,
            max_length = MAX_LEN,     
            pad_to_max_length = True,
            return_attention_mask = True,  
            return_tensors = 'pt' # return pytorch tensors
       )


encoded_instance

/usr/local/lib/python3.7/dist-packages/transformers/tokenization_utils_base.py:2111: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  FutureWarning,


{'input_ids': tensor([[    0,  1061,   642,   242,   107, 44679,   214,    70, 16648,     6,
             4,   200, 41324,  4420,     6,     4,   136,   756,   111,    10,
             2]]), 'attention_mask': tensor([[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]])}

In [12]:
print("Original text:", train.iloc[0].sentence)
print("BERT BPEs:", bert_tokenizer.convert_ids_to_tokens(encoded_instance["input_ids"][0]))

Original text: So we 're scoping the situation , kicking back , and all of a sudden this guy gets this insane barrel , then does a full - on airplane floater , then a full - on wraparound cutback , then a full - on snap reentry 
BERT BPEs: ['<s>', '▁So', '▁we', "▁'", 're', '▁scop', 'ing', '▁the', '▁situation', '▁', ',', '▁ki', 'cking', '▁back', '▁', ',', '▁and', '▁all', '▁of', '▁a', '</s>']


In [13]:
# Set max_len to the maximum length of the training data 
max_len = max([len(bert_tokenizer.encode(s)) for s in train.sentence.to_list()])
print("The maximum sentence length in training based on BERT BPEs is", max_len)

The maximum sentence length in training based on BERT BPEs is 118


In [14]:
# Tokenize and encode sentences in each set
x_train = bert_tokenizer.batch_encode_plus(
    train.sentence.tolist(),
    max_length = max_len,
    padding=True,
    truncation=True
)
x_val = bert_tokenizer.batch_encode_plus(
    val.sentence.tolist(),
    max_length = max_len,
    padding=True,
    truncation=True
)
x_test = bert_tokenizer.batch_encode_plus(
    test.sentence.tolist(),
    max_length = max_len,
    padding=True,
    truncation=True
)

In [15]:
# Convert lists to tensors in order to feed them to our PyTorch model
train_seq = torch.tensor(x_train['input_ids'])
train_mask = torch.tensor(x_train['attention_mask'])
train_y = torch.tensor(train.label.tolist())

val_seq = torch.tensor(x_val['input_ids'])
val_mask = torch.tensor(x_val['attention_mask'])
val_y = torch.tensor(val.label.tolist())

test_seq = torch.tensor(x_test['input_ids'])
test_mask = torch.tensor(x_test['attention_mask'])
test_y = torch.tensor(test.label.tolist())

In [16]:
batch_size = 32

# Create a dataloader for each set

# TensorDataset: Creates a PyTorch dataset object to load data from
train_data = TensorDataset(train_seq, train_mask, train_y)
# RandomSampler: specify the sequence of indices/keys used in data loading
train_sampler = RandomSampler(train_data)
# DataLoader: a Python iterable over a dataset
train_dataloader = DataLoader(train_data, sampler=train_sampler, batch_size=batch_size)

val_data = TensorDataset(val_seq, val_mask, val_y)
val_sampler = SequentialSampler(val_data)
val_dataloader = DataLoader(val_data, sampler=val_sampler, batch_size=batch_size)

test_data = TensorDataset(test_seq, test_mask, test_y)
test_sampler = SequentialSampler(test_data)
test_dataloader = DataLoader(test_data, sampler=test_sampler, batch_size=1)

## Inference

#### Load the saved checkpoint

In [17]:
model_e = model_e.to(device)

#### Get predictions for test

In [18]:
# Predict for the test set and save the results
model_e.eval()
test_predictions = []
test_targets = []
test_attentions = []
test_inputs = []

for batch in test_dataloader:
  batch = [t.to(device) for t in batch]
  sent_id, mask, labels = batch
  # Get gold labels
  test_targets.extend(labels.detach().cpu().numpy())
  # Get input words
  test_inputs.append(bert_tokenizer.convert_ids_to_tokens(sent_id.detach().cpu().numpy()[0]))
  with torch.no_grad():
    # Get predictions
    outputs = model_e(sent_id, attention_mask=mask)
    # Apply softmax to the outputs
    output_probs = softmax(outputs.logits.detach().cpu().numpy(), axis=1)
    # Get the with the highest probability as the predicted label
    test_predictions.extend(np.argmax(output_probs, axis=1))
    # Get attention weights
    # Attention weights from all layers are returned in a tuple
    # The weights from each layer are in a tensor with shape (batch_size, attention_heads, max_len, max_len)
    test_attentions.append(outputs.attentions)

#### Evaluate

In [20]:
print("F1:", f1_score(test_targets, test_predictions, average="binary"))
print("ACC:", accuracy_score(test_targets, test_predictions))
print("AUPR:", average_precision_score(test_targets, test_predictions))
print("PRECISION:", precision_score(test_targets, test_predictions))
print("RECALL:", recall_score(test_targets, test_predictions))
print("AUC:", roc_auc_score(test_targets, test_predictions))

F1: 0.9488054607508533
ACC: 0.9598930481283422
AUPR: 0.9243903593802174
PRECISION: 0.9586206896551724
RECALL: 0.9391891891891891
AUC: 0.9563202583114087


## Attention analysis


In [ ]:
# Get attention heatmaps
import matplotlib
from IPython.core.display import display, HTML
def colorize(words, color_array):
    cmap=matplotlib.cm.Reds
    template = '<span class="barcode"; style="color: black; background-color: {}">{}</span>'
    colored_string = ''
    for word, color in zip(words, color_array):
        color = matplotlib.colors.rgb2hex(cmap(color)[:3])
        colored_string += template.format(color, '&nbsp' + word + '&nbsp')
    return colored_string

In [ ]:
#max pooling to generate a fixed sized sentence embedding


#Max Pooling - Take the max value over time for every dimension
def max_pooling(model_output, attention_mask):
    token_embeddings = model_output[0] #First element of model_output contains all token embeddings
    input_mask_expanded = attention_mask.resize_(token_embeddings.size())
    #input_mask_expanded = attention_mask.unsqueeze(-1).expand(token_embeddings.size()).float()
    token_embeddings[input_mask_expanded == 0] = -1e9  # Set padding tokens to large negative value
    max_over_time = torch.max(token_embeddings, 1)[0]
    return max_over_time

def avg_pooling(model_output, attention_mask):
    token_embeddings = model_output[0] #First element of model_output contains all token embeddings
    input_mask_expanded = attention_mask.resize_(token_embeddings.size())
    #input_mask_expanded = attention_mask.unsqueeze(-1).expand(token_embeddings.size()).float()
    token_embeddings[input_mask_expanded == 0] = -1e9  # Set padding tokens to large negative value
    avg_over_time = torch.mean(token_embeddings, 1)[0]
    return avg_over_time


#Sentences we want sentence embeddings for
sentences = ['The', 'stars', 'gravitate', 'towards', 'each', 'other.']

#Tokenize sentences
encoded_input = bert_tokenizer(sentences, padding=True, truncation=True, max_length=128, return_tensors='pt')
encoded_input = encoded_input.to(device)

#Compute token embeddings
with torch.no_grad():
    model_output = model_e(**encoded_input)

#Perform pooling. In this case, max pooling
sentence_embeddings = max_pooling(model_output, encoded_input['attention_mask'])
#avg_sentence_embeddings = avg_pooling(model_output, encoded_input['attention_mask'])


print("Sentence embeddings:")
print(sentence_embeddings)

Sentence embeddings:
tensor([ 0.6841, -1.5802,  0.1865,  3.4566,  2.4093,  2.3109], device='cuda:0')


In [ ]:
# numpy implementation of argmax
from numpy import argmax

sentence_embeddings = sentence_embeddings.cpu()

# get argmax
result = argmax(sentence_embeddings)
print('arg max of %s: %d' % (sentence_embeddings, result))

arg max of tensor([ 0.6841, -1.5802,  0.1865,  3.4566,  2.4093,  2.3109]): 3


In [ ]:
#CLS token of each input represents the sentence embedding


#Sentences we want sentence embeddings for
sentences = ['The', 'stars', 'gravitate', 'towards', 'each', 'other']


#Tokenize sentences
encoded_input = bert_tokenizer(sentences, padding=True, truncation=True, max_length=128, return_tensors='pt')
encoded_input = encoded_input.to(device)

#Compute token embeddings
with torch.no_grad():
    model_output = model_e(**encoded_input)
    #model_output = model_output.to(device)
    
sentence_embeddings = model_output[0][:,0] #Take the first token ([CLS]) from each sentence 

print("Sentence embeddings:")
print(sentence_embeddings)

Sentence embeddings:
tensor([-0.6585, -1.5802,  0.1865,  3.4566,  2.4093, -0.6512], device='cuda:0')


In [ ]:
# numpy implementation of argmax
from numpy import argmax

sentence_embeddings = sentence_embeddings.cpu()

# get argmax
result = argmax(sentence_embeddings)
print('arg max of %s: %d' % (sentence_embeddings, result))

arg max of tensor([-0.6585, -1.5802,  0.1865,  3.4566,  2.4093, -0.6512]): 3


#### What does the CLS token attend to?




In [ ]:
# Original Loop

# Select some sentences randomly
sent_index = [0, 1, 2]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    for h, head in enumerate(attention):
      print("Head", h+1)
      # Get the attention for the cls token
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
    

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
# Max Pooling for all tokens in sentences and argmax

# Select some sentences randomly
sent_index = [0,1,2,3,4,5,6,7,8,9,10]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, truncation=True, padding=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = max_pooling(model_output1, encoded_tokens['attention_mask'])
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

****************************************************************************************************

Layer 1


Tokens embeddings:
tensor([ 8.9196e-02, -3.5529e-01,  8.6478e-01, -3.8012e+00,  1.4590e+00,
         4.2899e-01,  1.4181e+00,  3.1819e-01,  1.4342e-01,  3.8534e-01,
         8.6478e-01, -1.8008e+00,  1.4590e+00, -1.6799e+00,  1.5168e-01,
        -1.7484e+00,  1.4590e+00,  8.8022e-01,  4.2482e-01,  8.0017e-01,
         1.4191e+00, -1.8253e+00,  2.1204e+00, -3.5008e+00,  5.3103e-01,
        -1.7293e+00,  7.2058e-03, -1.6527e+00,  2.0505e-01, -1.0000e+09,
         1.4181e+00,  1.4250e-01,  7.2337e-01, -1.2851e-01,  1.1981e-01,
         3.6412e+00,  7.2058e-03, -2.1856e-01,  1.0131e+00,  5.4395e-01,
         7.2058e-03, -2.9728e-03,  2.5005e-01,  1.4181e+00,  1.5168e-01,
        -1.0216e-01,  6.6450e-02,  7.2337e-01,  1.1383e-01, -9.9737e-02,
         1.6223e-01,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02

Tokens embeddings:
tensor([ 8.9196e-02, -3.5529e-01,  8.6478e-01, -3.8012e+00,  1.4590e+00,
         4.2899e-01,  1.4181e+00,  3.1819e-01,  1.4342e-01,  3.8534e-01,
         8.6478e-01, -1.8008e+00,  1.4590e+00, -1.6799e+00,  1.5168e-01,
        -1.7484e+00,  1.4590e+00,  8.8022e-01,  4.2482e-01,  8.0017e-01,
         1.4191e+00, -1.8253e+00,  2.1204e+00, -3.5008e+00,  5.3103e-01,
        -1.7293e+00,  7.2058e-03, -1.6527e+00,  2.0505e-01, -1.0000e+09,
         1.4181e+00,  1.4250e-01,  7.2337e-01, -1.2851e-01,  1.1981e-01,
         3.6412e+00,  7.2058e-03, -2.1856e-01,  1.0131e+00,  5.4395e-01,
         7.2058e-03, -2.9728e-03,  2.5005e-01,  1.4181e+00,  1.5168e-01,
        -1.0216e-01,  6.6450e-02,  7.2337e-01,  1.1383e-01, -9.9737e-02,
         1.6223e-01,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02

Tokens embeddings:
tensor([ 8.9196e-02, -3.5529e-01,  8.6478e-01, -3.8012e+00,  1.4590e+00,
         4.2899e-01,  1.4181e+00,  3.1819e-01,  1.4342e-01,  3.8534e-01,
         8.6478e-01, -1.8008e+00,  1.4590e+00, -1.6799e+00,  1.5168e-01,
        -1.7484e+00,  1.4590e+00,  8.8022e-01,  4.2482e-01,  8.0017e-01,
         1.4191e+00, -1.8253e+00,  2.1204e+00, -3.5008e+00,  5.3103e-01,
        -1.7293e+00,  7.2058e-03, -1.6527e+00,  2.0505e-01, -1.0000e+09,
         1.4181e+00,  1.4250e-01,  7.2337e-01, -1.2851e-01,  1.1981e-01,
         3.6412e+00,  7.2058e-03, -2.1856e-01,  1.0131e+00,  5.4395e-01,
         7.2058e-03, -2.9728e-03,  2.5005e-01,  1.4181e+00,  1.5168e-01,
        -1.0216e-01,  6.6450e-02,  7.2337e-01,  1.1383e-01, -9.9737e-02,
         1.6223e-01,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02

Tokens embeddings:
tensor([ 8.9196e-02, -3.5529e-01,  8.6478e-01, -3.8012e+00,  1.4590e+00,
         4.2899e-01,  1.4181e+00,  3.1819e-01,  1.4342e-01,  3.8534e-01,
         8.6478e-01, -1.8008e+00,  1.4590e+00, -1.6799e+00,  1.5168e-01,
        -1.7484e+00,  1.4590e+00,  8.8022e-01,  4.2482e-01,  8.0017e-01,
         1.4191e+00, -1.8253e+00,  2.1204e+00, -3.5008e+00,  5.3103e-01,
        -1.7293e+00,  7.2058e-03, -1.6527e+00,  2.0505e-01, -1.0000e+09,
         1.4181e+00,  1.4250e-01,  7.2337e-01, -1.2851e-01,  1.1981e-01,
         3.6412e+00,  7.2058e-03, -2.1856e-01,  1.0131e+00,  5.4395e-01,
         7.2058e-03, -2.9728e-03,  2.5005e-01,  1.4181e+00,  1.5168e-01,
        -1.0216e-01,  6.6450e-02,  7.2337e-01,  1.1383e-01, -9.9737e-02,
         1.6223e-01,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02

...

Tokens embeddings:
tensor([ 8.9196e-02,  7.2943e-02,  7.2058e-03,  1.4307e-01,  1.2132e-01,
        -9.6701e-01,  3.8123e+00, -1.3761e+00,  1.9237e-01, -2.3550e+00,
         1.5168e-01, -1.7484e+00,  1.4590e+00, -1.1836e+00,  1.5667e+00,
        -6.1354e-01,  2.0463e-01, -3.0551e+00,  2.9017e-01,  1.4997e-01,
         5.0715e-01, -1.0000e+09,  1.5168e-01,  1.9107e+00,  1.1773e+00,
        -2.0047e+00,  3.5917e+00, -5.7711e-01,  1.8237e+00, -1.8008e+00,
         1.4590e+00,  2.1222e+00,  1.5168e-01, -1.7484e+00,  6.2986e-01,
         1.4942e+00,  3.4654e+00, -5.3814e-02,  3.4725e-01,  1.4181e+00,
         8.8168e-01,  8.8227e-01,  8.2517e-02, -1.8008e+00,  3.5948e+00,
        -1.0000e+09,  1.4590e+00,  4.1610e-01,  1.4406e+00, -9.9737e-02,
         1.2108e+00,  8.5115e-01,  8.6352e-01, -1.1622e+00,  5.4090e-01,
         7.4964e-01,  1.6223e-01,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
        -1.0000e+09,  2.1555e-02

Tokens embeddings:
tensor([ 8.9196e-02,  7.2943e-02,  7.2058e-03,  1.4307e-01,  1.2132e-01,
        -9.6701e-01,  3.8123e+00, -1.3761e+00,  1.9237e-01, -2.3550e+00,
         1.5168e-01, -1.7484e+00,  1.4590e+00, -1.1836e+00,  1.5667e+00,
        -6.1354e-01,  2.0463e-01, -3.0551e+00,  2.9017e-01,  1.4997e-01,
         5.0715e-01, -1.0000e+09,  1.5168e-01,  1.9107e+00,  1.1773e+00,
        -2.0047e+00,  3.5917e+00, -5.7711e-01,  1.8237e+00, -1.8008e+00,
         1.4590e+00,  2.1222e+00,  1.5168e-01, -1.7484e+00,  6.2986e-01,
         1.4942e+00,  3.4654e+00, -5.3814e-02,  3.4725e-01,  1.4181e+00,
         8.8168e-01,  8.8227e-01,  8.2517e-02, -1.8008e+00,  3.5948e+00,
        -1.0000e+09,  1.4590e+00,  4.1610e-01,  1.4406e+00, -9.9737e-02,
         1.2108e+00,  8.5115e-01,  8.6352e-01, -1.1622e+00,  5.4090e-01,
         7.4964e-01,  1.6223e-01,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
        -1.0000e+09,  2.1555e-02

Tokens embeddings:
tensor([ 8.9196e-02,  7.2943e-02,  7.2058e-03,  1.4307e-01,  1.2132e-01,
        -9.6701e-01,  3.8123e+00, -1.3761e+00,  1.9237e-01, -2.3550e+00,
         1.5168e-01, -1.7484e+00,  1.4590e+00, -1.1836e+00,  1.5667e+00,
        -6.1354e-01,  2.0463e-01, -3.0551e+00,  2.9017e-01,  1.4997e-01,
         5.0715e-01, -1.0000e+09,  1.5168e-01,  1.9107e+00,  1.1773e+00,
        -2.0047e+00,  3.5917e+00, -5.7711e-01,  1.8237e+00, -1.8008e+00,
         1.4590e+00,  2.1222e+00,  1.5168e-01, -1.7484e+00,  6.2986e-01,
         1.4942e+00,  3.4654e+00, -5.3814e-02,  3.4725e-01,  1.4181e+00,
         8.8168e-01,  8.8227e-01,  8.2517e-02, -1.8008e+00,  3.5948e+00,
        -1.0000e+09,  1.4590e+00,  4.1610e-01,  1.4406e+00, -9.9737e-02,
         1.2108e+00,  8.5115e-01,  8.6352e-01, -1.1622e+00,  5.4090e-01,
         7.4964e-01,  1.6223e-01,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
        -1.0000e+09,  2.1555e-02

Tokens embeddings:
tensor([ 8.9196e-02,  7.2943e-02,  7.2058e-03,  1.4307e-01,  1.2132e-01,
        -9.6701e-01,  3.8123e+00, -1.3761e+00,  1.9237e-01, -2.3550e+00,
         1.5168e-01, -1.7484e+00,  1.4590e+00, -1.1836e+00,  1.5667e+00,
        -6.1354e-01,  2.0463e-01, -3.0551e+00,  2.9017e-01,  1.4997e-01,
         5.0715e-01, -1.0000e+09,  1.5168e-01,  1.9107e+00,  1.1773e+00,
        -2.0047e+00,  3.5917e+00, -5.7711e-01,  1.8237e+00, -1.8008e+00,
         1.4590e+00,  2.1222e+00,  1.5168e-01, -1.7484e+00,  6.2986e-01,
         1.4942e+00,  3.4654e+00, -5.3814e-02,  3.4725e-01,  1.4181e+00,
         8.8168e-01,  8.8227e-01,  8.2517e-02, -1.8008e+00,  3.5948e+00,
        -1.0000e+09,  1.4590e+00,  4.1610e-01,  1.4406e+00, -9.9737e-02,
         1.2108e+00,  8.5115e-01,  8.6352e-01, -1.1622e+00,  5.4090e-01,
         7.4964e-01,  1.6223e-01,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
        -1.0000e+09,  2.1555e-02

Tokens embeddings:
tensor([ 8.9196e-02,  7.2943e-02,  7.2058e-03,  1.4307e-01,  1.2132e-01,
        -9.6701e-01,  3.8123e+00, -1.3761e+00,  1.9237e-01, -2.3550e+00,
         1.5168e-01, -1.7484e+00,  1.4590e+00, -1.1836e+00,  1.5667e+00,
        -6.1354e-01,  2.0463e-01, -3.0551e+00,  2.9017e-01,  1.4997e-01,
         5.0715e-01, -1.0000e+09,  1.5168e-01,  1.9107e+00,  1.1773e+00,
        -2.0047e+00,  3.5917e+00, -5.7711e-01,  1.8237e+00, -1.8008e+00,
         1.4590e+00,  2.1222e+00,  1.5168e-01, -1.7484e+00,  6.2986e-01,
         1.4942e+00,  3.4654e+00, -5.3814e-02,  3.4725e-01,  1.4181e+00,
         8.8168e-01,  8.8227e-01,  8.2517e-02, -1.8008e+00,  3.5948e+00,
        -1.0000e+09,  1.4590e+00,  4.1610e-01,  1.4406e+00, -9.9737e-02,
         1.2108e+00,  8.5115e-01,  8.6352e-01, -1.1622e+00,  5.4090e-01,
         7.4964e-01,  1.6223e-01,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
        -1.0000e+09,  2.1555e-02

In [ ]:
# Select some sentences randomly
sent_index = [11,12,13,14,15,16,17,18,19,20]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, truncation=True, padding=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = max_pooling(model_output1, encoded_tokens['attention_mask'])
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

****************************************************************************************************

Layer 1


Tokens embeddings:
tensor([ 8.9196e-02,  7.2943e-02,  3.3358e-01,  3.8123e+00,  1.4590e+00,
         3.8568e+00,  1.8014e-01,  1.4181e+00,  7.2058e-03,  1.5921e+00,
         1.5168e-01, -1.7484e+00,  1.4590e+00,  9.7091e-01,  1.4406e+00,
        -9.9737e-02,  3.2610e-02, -1.6272e-01, -1.9352e-02, -9.9737e-02,
         3.6139e+00, -1.0000e+09,  1.4590e+00,  7.3063e-01,  1.4406e+00,
        -9.9737e-02,  6.0863e-01, -1.1704e+00,  6.9614e-01, -4.0324e-01,
         4.1290e+00, -1.3761e+00,  3.4961e+00, -1.7293e+00,  1.4590e+00,
         6.6049e-01,  1.6840e+00,  9.8942e-02,  3.6078e-01, -1.3587e+00,
         3.8721e-02, -5.1228e-02,  2.5608e+00,  1.3118e+00,  1.9773e+00,
        -1.4979e+00,  1.1519e+00,  1.2434e+00,  7.2058e-03, -7.5079e-01,
         8.4467e-01, -8.6117e-01,  8.1077e-01,  3.7816e-01,  1.6223e-01,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02

Tokens embeddings:
tensor([ 8.9196e-02,  7.2943e-02,  3.3358e-01,  3.8123e+00,  1.4590e+00,
         3.8568e+00,  1.8014e-01,  1.4181e+00,  7.2058e-03,  1.5921e+00,
         1.5168e-01, -1.7484e+00,  1.4590e+00,  9.7091e-01,  1.4406e+00,
        -9.9737e-02,  3.2610e-02, -1.6272e-01, -1.9352e-02, -9.9737e-02,
         3.6139e+00, -1.0000e+09,  1.4590e+00,  7.3063e-01,  1.4406e+00,
        -9.9737e-02,  6.0863e-01, -1.1704e+00,  6.9614e-01, -4.0324e-01,
         4.1290e+00, -1.3761e+00,  3.4961e+00, -1.7293e+00,  1.4590e+00,
         6.6049e-01,  1.6840e+00,  9.8942e-02,  3.6078e-01, -1.3587e+00,
         3.8721e-02, -5.1228e-02,  2.5608e+00,  1.3118e+00,  1.9773e+00,
        -1.4979e+00,  1.1519e+00,  1.2434e+00,  7.2058e-03, -7.5079e-01,
         8.4467e-01, -8.6117e-01,  8.1077e-01,  3.7816e-01,  1.6223e-01,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02

Tokens embeddings:
tensor([ 8.9196e-02,  7.2943e-02,  3.3358e-01,  3.8123e+00,  1.4590e+00,
         3.8568e+00,  1.8014e-01,  1.4181e+00,  7.2058e-03,  1.5921e+00,
         1.5168e-01, -1.7484e+00,  1.4590e+00,  9.7091e-01,  1.4406e+00,
        -9.9737e-02,  3.2610e-02, -1.6272e-01, -1.9352e-02, -9.9737e-02,
         3.6139e+00, -1.0000e+09,  1.4590e+00,  7.3063e-01,  1.4406e+00,
        -9.9737e-02,  6.0863e-01, -1.1704e+00,  6.9614e-01, -4.0324e-01,
         4.1290e+00, -1.3761e+00,  3.4961e+00, -1.7293e+00,  1.4590e+00,
         6.6049e-01,  1.6840e+00,  9.8942e-02,  3.6078e-01, -1.3587e+00,
         3.8721e-02, -5.1228e-02,  2.5608e+00,  1.3118e+00,  1.9773e+00,
        -1.4979e+00,  1.1519e+00,  1.2434e+00,  7.2058e-03, -7.5079e-01,
         8.4467e-01, -8.6117e-01,  8.1077e-01,  3.7816e-01,  1.6223e-01,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02

Tokens embeddings:
tensor([ 8.9196e-02,  7.2943e-02,  3.3358e-01,  3.8123e+00,  1.4590e+00,
         3.8568e+00,  1.8014e-01,  1.4181e+00,  7.2058e-03,  1.5921e+00,
         1.5168e-01, -1.7484e+00,  1.4590e+00,  9.7091e-01,  1.4406e+00,
        -9.9737e-02,  3.2610e-02, -1.6272e-01, -1.9352e-02, -9.9737e-02,
         3.6139e+00, -1.0000e+09,  1.4590e+00,  7.3063e-01,  1.4406e+00,
        -9.9737e-02,  6.0863e-01, -1.1704e+00,  6.9614e-01, -4.0324e-01,
         4.1290e+00, -1.3761e+00,  3.4961e+00, -1.7293e+00,  1.4590e+00,
         6.6049e-01,  1.6840e+00,  9.8942e-02,  3.6078e-01, -1.3587e+00,
         3.8721e-02, -5.1228e-02,  2.5608e+00,  1.3118e+00,  1.9773e+00,
        -1.4979e+00,  1.1519e+00,  1.2434e+00,  7.2058e-03, -7.5079e-01,
         8.4467e-01, -8.6117e-01,  8.1077e-01,  3.7816e-01,  1.6223e-01,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02

...

Tokens embeddings:
tensor([ 8.9196e-02,  9.1228e-02,  3.8123e+00, -1.9195e+00,  1.4590e+00,
        -7.3155e-01,  3.8534e-01,  8.6478e-01,  7.2058e-03,  3.6490e+00,
         2.0537e+00, -1.1622e+00,  1.7838e+00, -4.3494e-01,  6.8475e-01,
        -3.5008e+00,  3.3001e+00,  2.1852e+00,  6.8134e-01, -1.5615e+00,
         4.0618e-01,  1.5168e-01,  3.3658e+00, -1.3587e+00,  1.6223e-01,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02, -1.0000e+09,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02

Tokens embeddings:
tensor([ 8.9196e-02,  9.1228e-02,  3.8123e+00, -1.9195e+00,  1.4590e+00,
        -7.3155e-01,  3.8534e-01,  8.6478e-01,  7.2058e-03,  3.6490e+00,
         2.0537e+00, -1.1622e+00,  1.7838e+00, -4.3494e-01,  6.8475e-01,
        -3.5008e+00,  3.3001e+00,  2.1852e+00,  6.8134e-01, -1.5615e+00,
         4.0618e-01,  1.5168e-01,  3.3658e+00, -1.3587e+00,  1.6223e-01,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02, -1.0000e+09,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02

Tokens embeddings:
tensor([ 8.9196e-02,  9.1228e-02,  3.8123e+00, -1.9195e+00,  1.4590e+00,
        -7.3155e-01,  3.8534e-01,  8.6478e-01,  7.2058e-03,  3.6490e+00,
         2.0537e+00, -1.1622e+00,  1.7838e+00, -4.3494e-01,  6.8475e-01,
        -3.5008e+00,  3.3001e+00,  2.1852e+00,  6.8134e-01, -1.5615e+00,
         4.0618e-01,  1.5168e-01,  3.3658e+00, -1.3587e+00,  1.6223e-01,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02, -1.0000e+09,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02

Tokens embeddings:
tensor([ 8.9196e-02,  9.1228e-02,  3.8123e+00, -1.9195e+00,  1.4590e+00,
        -7.3155e-01,  3.8534e-01,  8.6478e-01,  7.2058e-03,  3.6490e+00,
         2.0537e+00, -1.1622e+00,  1.7838e+00, -4.3494e-01,  6.8475e-01,
        -3.5008e+00,  3.3001e+00,  2.1852e+00,  6.8134e-01, -1.5615e+00,
         4.0618e-01,  1.5168e-01,  3.3658e+00, -1.3587e+00,  1.6223e-01,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02, -1.0000e+09,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02

Tokens embeddings:
tensor([ 8.9196e-02,  9.1228e-02,  3.8123e+00, -1.9195e+00,  1.4590e+00,
        -7.3155e-01,  3.8534e-01,  8.6478e-01,  7.2058e-03,  3.6490e+00,
         2.0537e+00, -1.1622e+00,  1.7838e+00, -4.3494e-01,  6.8475e-01,
        -3.5008e+00,  3.3001e+00,  2.1852e+00,  6.8134e-01, -1.5615e+00,
         4.0618e-01,  1.5168e-01,  3.3658e+00, -1.3587e+00,  1.6223e-01,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02, -1.0000e+09,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02

In [ ]:
# Max Pooling for all tokens in sentences and argmax

# Select some sentences randomly
sent_index = [21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48,49,50,51,52,53,54,55,56,57,58,59,60,61,62,63,64]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, truncation=True, padding=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = max_pooling(model_output1, encoded_tokens['attention_mask'])
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
# Pooling First token [CLS] for each sentence - argmax

# Select some sentences randomly
sent_index = [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #for h, head in enumerate(attention):
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, padding=True, truncation=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = model_output1[0][:,0]
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

****************************************************************************************************

Layer 1


Tokens embeddings:
tensor([-9.3286e-02, -3.5529e-01,  8.6478e-01, -3.8012e+00, -1.3761e+00,
         4.2899e-01,  1.4181e+00,  3.1819e-01,  1.4342e-01,  3.8534e-01,
         8.6478e-01, -1.8008e+00, -1.3761e+00, -1.6799e+00,  1.5168e-01,
        -1.7484e+00, -1.3761e+00,  8.8022e-01, -4.1868e-01,  8.0017e-01,
         1.4191e+00, -1.8253e+00, -1.9505e+00, -3.5008e+00, -5.0294e-01,
        -1.7293e+00, -5.4771e-02, -1.6527e+00,  2.0505e-01,  1.1760e+00,
         1.4181e+00, -1.3624e-01,  7.2337e-01, -1.2851e-01, -9.9737e-02,
         3.6412e+00, -5.4771e-02, -2.1856e-01,  1.0131e+00,  5.4395e-01,
        -5.4771e-02, -2.9728e-03,  2.5005e-01,  1.4181e+00,  1.5168e-01,
        -1.0216e-01, -5.5815e-02,  7.2337e-01, -1.2851e-01, -9.9737e-02,
         1.6223e-01,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02

Tokens embeddings:
tensor([-9.3286e-02, -3.5529e-01,  8.6478e-01, -3.8012e+00, -1.3761e+00,
         4.2899e-01,  1.4181e+00,  3.1819e-01,  1.4342e-01,  3.8534e-01,
         8.6478e-01, -1.8008e+00, -1.3761e+00, -1.6799e+00,  1.5168e-01,
        -1.7484e+00, -1.3761e+00,  8.8022e-01, -4.1868e-01,  8.0017e-01,
         1.4191e+00, -1.8253e+00, -1.9505e+00, -3.5008e+00, -5.0294e-01,
        -1.7293e+00, -5.4771e-02, -1.6527e+00,  2.0505e-01,  1.1760e+00,
         1.4181e+00, -1.3624e-01,  7.2337e-01, -1.2851e-01, -9.9737e-02,
         3.6412e+00, -5.4771e-02, -2.1856e-01,  1.0131e+00,  5.4395e-01,
        -5.4771e-02, -2.9728e-03,  2.5005e-01,  1.4181e+00,  1.5168e-01,
        -1.0216e-01, -5.5815e-02,  7.2337e-01, -1.2851e-01, -9.9737e-02,
         1.6223e-01,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02

Tokens embeddings:
tensor([-9.3286e-02, -3.5529e-01,  8.6478e-01, -3.8012e+00, -1.3761e+00,
         4.2899e-01,  1.4181e+00,  3.1819e-01,  1.4342e-01,  3.8534e-01,
         8.6478e-01, -1.8008e+00, -1.3761e+00, -1.6799e+00,  1.5168e-01,
        -1.7484e+00, -1.3761e+00,  8.8022e-01, -4.1868e-01,  8.0017e-01,
         1.4191e+00, -1.8253e+00, -1.9505e+00, -3.5008e+00, -5.0294e-01,
        -1.7293e+00, -5.4771e-02, -1.6527e+00,  2.0505e-01,  1.1760e+00,
         1.4181e+00, -1.3624e-01,  7.2337e-01, -1.2851e-01, -9.9737e-02,
         3.6412e+00, -5.4771e-02, -2.1856e-01,  1.0131e+00,  5.4395e-01,
        -5.4771e-02, -2.9728e-03,  2.5005e-01,  1.4181e+00,  1.5168e-01,
        -1.0216e-01, -5.5815e-02,  7.2337e-01, -1.2851e-01, -9.9737e-02,
         1.6223e-01,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02

Tokens embeddings:
tensor([-9.3286e-02, -3.5529e-01,  8.6478e-01, -3.8012e+00, -1.3761e+00,
         4.2899e-01,  1.4181e+00,  3.1819e-01,  1.4342e-01,  3.8534e-01,
         8.6478e-01, -1.8008e+00, -1.3761e+00, -1.6799e+00,  1.5168e-01,
        -1.7484e+00, -1.3761e+00,  8.8022e-01, -4.1868e-01,  8.0017e-01,
         1.4191e+00, -1.8253e+00, -1.9505e+00, -3.5008e+00, -5.0294e-01,
        -1.7293e+00, -5.4771e-02, -1.6527e+00,  2.0505e-01,  1.1760e+00,
         1.4181e+00, -1.3624e-01,  7.2337e-01, -1.2851e-01, -9.9737e-02,
         3.6412e+00, -5.4771e-02, -2.1856e-01,  1.0131e+00,  5.4395e-01,
        -5.4771e-02, -2.9728e-03,  2.5005e-01,  1.4181e+00,  1.5168e-01,
        -1.0216e-01, -5.5815e-02,  7.2337e-01, -1.2851e-01, -9.9737e-02,
         1.6223e-01,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,  2.1555e-02,
         2.1555e-02,  2.1555e-02

...

Tokens embeddings:
tensor([-0.0933,  0.0729, -0.0548,  0.1431, -0.1218, -0.9670,  3.8123, -1.3761,
         0.1924, -2.3550,  0.1517, -1.7484, -1.3761, -1.1836,  1.5667, -0.6135,
         0.2046, -3.0551, -0.2538,  0.1500, -0.5410, -0.5771,  0.1517, -1.7484,
         1.1773, -2.0047,  3.5917, -0.5771, -1.6273, -1.8008, -1.3761,  2.1222,
         0.1517, -1.7484, -0.6627,  1.4942,  3.4654, -0.0538, -0.3304,  1.4181,
        -0.8528,  0.8823,  0.0825, -1.8008,  3.5948, -1.4097, -1.3761, -0.4117,
        -1.3587, -0.0997, -1.1622,  0.8512, -0.8182, -1.1622, -0.5226,  0.7496,
         0.1622,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0

Tokens embeddings:
tensor([-0.0933,  0.0729, -0.0548,  0.1431, -0.1218, -0.9670,  3.8123, -1.3761,
         0.1924, -2.3550,  0.1517, -1.7484, -1.3761, -1.1836,  1.5667, -0.6135,
         0.2046, -3.0551, -0.2538,  0.1500, -0.5410, -0.5771,  0.1517, -1.7484,
         1.1773, -2.0047,  3.5917, -0.5771, -1.6273, -1.8008, -1.3761,  2.1222,
         0.1517, -1.7484, -0.6627,  1.4942,  3.4654, -0.0538, -0.3304,  1.4181,
        -0.8528,  0.8823,  0.0825, -1.8008,  3.5948, -1.4097, -1.3761, -0.4117,
        -1.3587, -0.0997, -1.1622,  0.8512, -0.8182, -1.1622, -0.5226,  0.7496,
         0.1622,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0

Tokens embeddings:
tensor([-0.0933,  0.0729, -0.0548,  0.1431, -0.1218, -0.9670,  3.8123, -1.3761,
         0.1924, -2.3550,  0.1517, -1.7484, -1.3761, -1.1836,  1.5667, -0.6135,
         0.2046, -3.0551, -0.2538,  0.1500, -0.5410, -0.5771,  0.1517, -1.7484,
         1.1773, -2.0047,  3.5917, -0.5771, -1.6273, -1.8008, -1.3761,  2.1222,
         0.1517, -1.7484, -0.6627,  1.4942,  3.4654, -0.0538, -0.3304,  1.4181,
        -0.8528,  0.8823,  0.0825, -1.8008,  3.5948, -1.4097, -1.3761, -0.4117,
        -1.3587, -0.0997, -1.1622,  0.8512, -0.8182, -1.1622, -0.5226,  0.7496,
         0.1622,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0

Tokens embeddings:
tensor([-0.0933,  0.0729, -0.0548,  0.1431, -0.1218, -0.9670,  3.8123, -1.3761,
         0.1924, -2.3550,  0.1517, -1.7484, -1.3761, -1.1836,  1.5667, -0.6135,
         0.2046, -3.0551, -0.2538,  0.1500, -0.5410, -0.5771,  0.1517, -1.7484,
         1.1773, -2.0047,  3.5917, -0.5771, -1.6273, -1.8008, -1.3761,  2.1222,
         0.1517, -1.7484, -0.6627,  1.4942,  3.4654, -0.0538, -0.3304,  1.4181,
        -0.8528,  0.8823,  0.0825, -1.8008,  3.5948, -1.4097, -1.3761, -0.4117,
        -1.3587, -0.0997, -1.1622,  0.8512, -0.8182, -1.1622, -0.5226,  0.7496,
         0.1622,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0

Tokens embeddings:
tensor([-0.0933,  0.0729, -0.0548,  0.1431, -0.1218, -0.9670,  3.8123, -1.3761,
         0.1924, -2.3550,  0.1517, -1.7484, -1.3761, -1.1836,  1.5667, -0.6135,
         0.2046, -3.0551, -0.2538,  0.1500, -0.5410, -0.5771,  0.1517, -1.7484,
         1.1773, -2.0047,  3.5917, -0.5771, -1.6273, -1.8008, -1.3761,  2.1222,
         0.1517, -1.7484, -0.6627,  1.4942,  3.4654, -0.0538, -0.3304,  1.4181,
        -0.8528,  0.8823,  0.0825, -1.8008,  3.5948, -1.4097, -1.3761, -0.4117,
        -1.3587, -0.0997, -1.1622,  0.8512, -0.8182, -1.1622, -0.5226,  0.7496,
         0.1622,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0

In [ ]:
# Pooling First token [CLS] for each sentence - argmax

# Select some sentences randomly
sent_index = [11, 12, 13, 14, 15, 16, 17, 18, 19, 20]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #for h, head in enumerate(attention):
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, padding=True, truncation=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = model_output1[0][:,0]
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

****************************************************************************************************

Layer 1


Tokens embeddings:
tensor([-0.0933,  0.0729, -0.2742,  3.8123, -1.3761,  3.8568, -0.2263,  1.4181,
        -0.0548,  1.5921,  0.1517, -1.7484, -1.3761,  0.9709, -1.3587, -0.0997,
        -0.0531, -0.1627, -0.0194, -0.0997,  3.6139, -3.3272, -1.3761,  0.7306,
        -1.3587, -0.0997,  0.6086, -1.1704,  0.6961, -0.4032, -3.8012, -1.3761,
         3.4961, -1.7293, -1.3761,  0.6605,  1.6840,  0.0989, -0.3250, -1.3587,
         0.0387, -0.0512, -2.4238,  1.3118, -1.8008, -1.4979, -1.0834,  1.2434,
        -0.0548, -0.7508, -0.8844, -0.8612, -0.7778,  0.3782,  0.1622,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0

Tokens embeddings:
tensor([-0.0933,  0.0729, -0.2742,  3.8123, -1.3761,  3.8568, -0.2263,  1.4181,
        -0.0548,  1.5921,  0.1517, -1.7484, -1.3761,  0.9709, -1.3587, -0.0997,
        -0.0531, -0.1627, -0.0194, -0.0997,  3.6139, -3.3272, -1.3761,  0.7306,
        -1.3587, -0.0997,  0.6086, -1.1704,  0.6961, -0.4032, -3.8012, -1.3761,
         3.4961, -1.7293, -1.3761,  0.6605,  1.6840,  0.0989, -0.3250, -1.3587,
         0.0387, -0.0512, -2.4238,  1.3118, -1.8008, -1.4979, -1.0834,  1.2434,
        -0.0548, -0.7508, -0.8844, -0.8612, -0.7778,  0.3782,  0.1622,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0

Tokens embeddings:
tensor([-0.0933,  0.0729, -0.2742,  3.8123, -1.3761,  3.8568, -0.2263,  1.4181,
        -0.0548,  1.5921,  0.1517, -1.7484, -1.3761,  0.9709, -1.3587, -0.0997,
        -0.0531, -0.1627, -0.0194, -0.0997,  3.6139, -3.3272, -1.3761,  0.7306,
        -1.3587, -0.0997,  0.6086, -1.1704,  0.6961, -0.4032, -3.8012, -1.3761,
         3.4961, -1.7293, -1.3761,  0.6605,  1.6840,  0.0989, -0.3250, -1.3587,
         0.0387, -0.0512, -2.4238,  1.3118, -1.8008, -1.4979, -1.0834,  1.2434,
        -0.0548, -0.7508, -0.8844, -0.8612, -0.7778,  0.3782,  0.1622,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0

Tokens embeddings:
tensor([-0.0933,  0.0729, -0.2742,  3.8123, -1.3761,  3.8568, -0.2263,  1.4181,
        -0.0548,  1.5921,  0.1517, -1.7484, -1.3761,  0.9709, -1.3587, -0.0997,
        -0.0531, -0.1627, -0.0194, -0.0997,  3.6139, -3.3272, -1.3761,  0.7306,
        -1.3587, -0.0997,  0.6086, -1.1704,  0.6961, -0.4032, -3.8012, -1.3761,
         3.4961, -1.7293, -1.3761,  0.6605,  1.6840,  0.0989, -0.3250, -1.3587,
         0.0387, -0.0512, -2.4238,  1.3118, -1.8008, -1.4979, -1.0834,  1.2434,
        -0.0548, -0.7508, -0.8844, -0.8612, -0.7778,  0.3782,  0.1622,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0

...

Tokens embeddings:
tensor([-0.0933,  0.0912,  3.8123, -1.9195, -1.3761, -0.7316,  0.3853,  0.8648,
        -0.0548,  3.6490, -1.9345, -1.1622, -1.6536, -0.4349, -0.6617, -3.5008,
         3.3001,  2.1852, -0.5915, -1.5615,  0.4062,  0.1517, -3.0551, -1.3587,
         0.1622,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0

Tokens embeddings:
tensor([-0.0933,  0.0912,  3.8123, -1.9195, -1.3761, -0.7316,  0.3853,  0.8648,
        -0.0548,  3.6490, -1.9345, -1.1622, -1.6536, -0.4349, -0.6617, -3.5008,
         3.3001,  2.1852, -0.5915, -1.5615,  0.4062,  0.1517, -3.0551, -1.3587,
         0.1622,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0

Tokens embeddings:
tensor([-0.0933,  0.0912,  3.8123, -1.9195, -1.3761, -0.7316,  0.3853,  0.8648,
        -0.0548,  3.6490, -1.9345, -1.1622, -1.6536, -0.4349, -0.6617, -3.5008,
         3.3001,  2.1852, -0.5915, -1.5615,  0.4062,  0.1517, -3.0551, -1.3587,
         0.1622,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0

Tokens embeddings:
tensor([-0.0933,  0.0912,  3.8123, -1.9195, -1.3761, -0.7316,  0.3853,  0.8648,
        -0.0548,  3.6490, -1.9345, -1.1622, -1.6536, -0.4349, -0.6617, -3.5008,
         3.3001,  2.1852, -0.5915, -1.5615,  0.4062,  0.1517, -3.0551, -1.3587,
         0.1622,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0

Tokens embeddings:
tensor([-0.0933,  0.0912,  3.8123, -1.9195, -1.3761, -0.7316,  0.3853,  0.8648,
        -0.0548,  3.6490, -1.9345, -1.1622, -1.6536, -0.4349, -0.6617, -3.5008,
         3.3001,  2.1852, -0.5915, -1.5615,  0.4062,  0.1517, -3.0551, -1.3587,
         0.1622,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,  0.0216,
         0.0216,  0.0

In [ ]:
# Pooling First token [CLS] for each sentence - argmax

# Select some sentences randomly
sent_index = [21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48,49,50,51,52,53,54,55,56,57,58,59,60,61,62,63,64]

for s in sent_index:
  print("*" * 100)
  # Get the sentence's words
  tokens = test_inputs[s]
  # For each layer...
  for l in range(12):
    print("\nLayer", l+1)
    attention = np.squeeze(test_attentions[s][l].detach().cpu().numpy(), axis=0)
    # and for each head
    #for h, head in enumerate(attention):
    #print("Head", h+1)
    # Get the attention for the cls token
    encoded_tokens = bert_tokenizer(tokens, padding=True, truncation=True, max_length=128, return_tensors='pt')
    encoded_tokens = encoded_tokens.to(device)
    with torch.no_grad():
      model_output1 = model_e(**encoded_tokens)
      tokens_embeddings = model_output1[0][:,0]
      tokens_embeddings = tokens_embeddings.cpu()
      cls_attentions = head[0]
      display(HTML(colorize(tokens, cls_attentions)))
      print("Tokens embeddings:")
      print(tokens_embeddings)
      arg = argmax(tokens_embeddings)
      print('arg max of %s: %d' % (tokens_embeddings, arg))

Output hidden; open in https://colab.research.google.com to view.

#### Visualize attentions for specific types of grammatical errors

In [ ]:
# Lack of Subject-Verb Agreement
sentence1 = "I wrestled with this decision for years ."
# Pronoun Disagreement
sentence2 = "lined books are more enduring ."

In [ ]:
# Encode the first sentence
encoded_sentence1 = bert_tokenizer.batch_encode_plus([sentence1], padding=True)

# Give as input to the model and get the outputs
inputs = torch.tensor(encoded_sentence1["input_ids"]).to(device)
att = torch.tensor(encoded_sentence1["attention_mask"]).to(device)
outputs = model_e(inputs, attention_mask=att)

In [ ]:
# Get the predictions
output_probs = softmax(outputs.logits.detach().cpu().numpy(), axis=1)
predictions = (np.argmax(output_probs, axis=1))
print(sentence1, ":", predictions[0])

I wrestled with this decision for years . : 1


In [ ]:
# Visualize the attention heatmaps for the CLS token
tokens = bert_tokenizer.convert_ids_to_tokens(inputs.detach().cpu().numpy()[0])
for l in range(12):
  print("\nLayer", l+1)
  attention = np.squeeze(outputs.attentions[l].detach().cpu().numpy(), axis=0)
  cls_attentions = []
  for h, head in enumerate(attention):
    print("Head", h+1)
    # Get the attention for the cls token
    cls_attentions = head[0]
    display(HTML(colorize(tokens, cls_attentions)))


Layer 1
Head 1


Head 2


Head 3


Head 4


Head 5


...

Head 8


Head 9


Head 10


Head 11


Head 12


In [ ]:
# Encode the second sentence
encoded_sentence2 = bert_tokenizer.batch_encode_plus([sentence2], padding=True)

# Give as input to the model and get the outputs
inputs = torch.tensor(encoded_sentence2["input_ids"]).to(device)
att = torch.tensor(encoded_sentence2["attention_mask"]).to(device)
outputs = model_e(inputs, attention_mask=att)

# Get the predictions
output_probs = softmax(outputs.logits.detach().cpu().numpy(), axis=1)
predictions = (np.argmax(output_probs, axis=1))
print(sentence2, ":", predictions[0])

lined books are more enduring . : 0


In [ ]:
# Visualize the attention heatmaps for the CLS token
tokens = bert_tokenizer.convert_ids_to_tokens(inputs.detach().cpu().numpy()[0])
for l in range(12):
  print("\nLayer", l+1)
  attention = np.squeeze(outputs.attentions[l].detach().cpu().numpy(), axis=0)
  cls_attentions = []
  for h, head in enumerate(attention):
    print("Head", h+1)
    # Get the attention for the cls token
    cls_attentions = head[0]
    display(HTML(colorize(tokens, cls_attentions)))


Layer 1
Head 1


Head 2


Head 3


Head 4


Head 5


...

Head 8


Head 9


Head 10


Head 11


Head 12
